In [1]:
import json 
import os
import logging 
import concurrent 
import asyncio 
import re 
import requests 

from pathlib import Path 
from itertools import chain 
from collections import namedtuple
from pprint import PrettyPrinter

from subgrounds import Subgrounds
from web3 import Web3
from concurrent.futures import ThreadPoolExecutor
from pycoingecko import CoinGeckoAPI

from prefect import flow, task
from prefect.tasks import task_input_hash
from prefect.filesystems import LocalFileSystem 
from prefect.orion.api.task_runs import read_task_run

import pandas as pd 
import numpy as np 
import altair as alt 
import missingno as miss

from flywheel_util.constants import (
    colors_24,
    colors_28, 
    addresses, 
    url_infura, 
    url_snapshot, 
    url_subgraphs, 
    snapshot_api_max_records_per_request, 
    snapshot_api_max_skip,
)
from flywheel_util.tasks import df_to_sql
from flywheel_util.utils import (
    ddf, 
    first_row, 
    camel_to_snake, 
    cg_get_market_history, 
    df_cols_camel_to_snake, 
    df_cols_change_prefix, 
    df_sort_cols, 
    remove_prefix, 
    graphql_execute, 
    remove_prefix, 
    remove_prefixes, 
    recursive_index_merge, 
    zip_dfs, 
    query_attrs, 
    compare_sets, 
    compare_cols, 
)
from flywheel_util.w3_utils import (
    get_verified_abi, 
    erc20_read_contract, 
    verified_contract
)
from sqlalchemy import create_engine
from sqlalchemy import text
engine = create_engine("sqlite+pysqlite:///votium_bribes.db", echo=False, future=True)

# logging.basicConfig(level=logging.INFO)

import logging
logging.basicConfig(level=logging.DEBUG)

# TODO: Figure out how this frax subgraph is useful
# https://api.thegraph.com/subgraphs/name/frax-finance-data/fraxbp-subgraph/graphql

pp = PrettyPrinter().pprint

alt.data_transformers.disable_max_rows()

/opt/miniconda3/envs/flywheel/lib/python3.10/site-packages/eth_utils/toolz.py:2: DeprecationWarning: The toolz.compatibility module is no longer needed in Python 3 and has been deprecated. Please import these utilities directly from the standard library. This module will be removed in a future release.
  from cytoolz import (
/opt/miniconda3/envs/flywheel/lib/python3.10/site-packages/web3/_utils/normalizers.py:231: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(eth_abi.__version__) < LooseVersion("2"):


DataTransformerRegistry.enable('default')

In [2]:
w3 = Web3(Web3.HTTPProvider(url_infura))
cg = CoinGeckoAPI()

# Bribes Analysis 

We are interested in analyzing the impact of bribes performed by the frax protocol through votium. Specifically, we aim to measure their ability to incentivize liquidity. 

Votium is a marketplace bringing together individual holders of vlCVX and protocols who wish to aggregate vlCVX so that gauges of their preference can receive a larger weight and thus a larger share of crv emissions (as well as emissions from platforms like convex built on top of curve). 

This analysis is focused primarily on the bribing strategy as it relates to the various FraxBP metapools. 

<!-- The following metrics are of interest

- \\$ Bribes spent per pool (broken down by platform and incentive type)  
- \\$ Liquidity per pool (broken into Frax and non-Frax components) 

Once we have both the liquidity and bribe information, we can try to answer these questions
- Where are bribe dollars best spent? 
- How does the Frax protocol optimize its bribing strategy in order to maximize the amount of liquidity within it's pools?  -->

In [3]:
sg = Subgrounds()

sg_curve_pools = sg.load_subgraph(url_subgraphs.convex.curve_pools) 
sg_curve_vol = sg.load_subgraph(url_subgraphs.convex.curve_vol_mainnet)
sg_votium = sg.load_subgraph(url_subgraphs.votium.bribes) 

## Curve Liquidity for FraxBP + FraxBP Metapools

In [4]:
%load_ext autoreload
%autoreload 2

from flywheel_util.curve_liquidity_tasks import (
    query_curve_mpools_with_gauge, 
    query_curve_pool_snapshots,
    query_curve_pool_vol_snapshots,
    query_metapool_paired_asset_global_volume,
    compute_pool_dfs,
    # compute_curve_pool_reserves,
    # join_curve_pool_vol,
    remove_inactive_pools,
    compute_metapool_snaps,
    remove_inactive_pools,
    # process_pool_data,
)

In [5]:
@flow(cache_result_in_memory=False)
def flow_fraxbp_metapool_data():
    # Retrieve data from api's / subgraphs 
    df_mpools_gauge = query_curve_mpools_with_gauge.submit()
    df_pool_snaps = query_curve_pool_snapshots.submit()
    df_pool_vol_snaps = query_curve_pool_vol_snapshots.submit()
        
    # df_pools is an id table for pools - primary key (pool_address) 
    # df_coins is an id table for coins in pools - primary key (pool_address, pool_coin_address) 
    # df_pool_coin joins together all info from df_pools and df_coins
    df_pools, df_coins, df_pool_coin = compute_pool_dfs(df_mpools_gauge, df_pool_snaps)    

    # Remove inactive pools 
    df_pools, df_pool_coin, df_pool_snaps, df_pool_vol_snaps = remove_inactive_pools(
        df_pools, df_coins, df_pool_coin, df_pool_snaps, df_pool_vol_snaps
    )
    
    # Contains daily snapshot data of pool reserves - primary key (date, pool_address, pool_coin_address)
    df_reserves = df_pool_snaps[[
        'date',
        'pool_address',
        'pool_coin_address',
        'reserves',
        'reserves_usd',
        'reserves_coin_price_usd',
    ]].drop_duplicates()
    assert all(
        len(gdf) == 1 for _, gdf in df_reserves.groupby(['date', 'pool_address', 'pool_coin_address'])
    )
    
    # Contains daily snapshot data for pool level metrics - primary key (date, pool_address) 
    df_pool_snaps = (
        df_pool_snaps[['date', 'pool_address', 'lp_price_usd', 'tvl']]
        .rename(columns={
            'tvl': 'snap_tvl_usd', 
            'lp_price_usd': 'snap_lp_price_usd', 
        })
        # drop duplicates since there was one row per pool and coin pre-filtering
        .drop_duplicates()     
        # Joins in pool swap volume 
        .merge(
            df_pool_vol_snaps.rename(columns={'snap_volume_usd': 'snap_vol_usd'}), 
            how='left', 
            on=['date', 'pool_address']
        )
    )
    df_pool_snaps.snap_vol_usd = df_pool_snaps.snap_vol_usd.fillna(0)
    assert not ((df_pool_snaps.snap_tvl_usd == 0) ^ (df_pool_snaps.snap_lp_price_usd == 0)).any()
    df_pool_snaps['snap_lp_supply'] = (df_pool_snaps.snap_tvl_usd / df_pool_snaps.snap_lp_price_usd).fillna(0)    
    df_pool_snaps['snap_liq_util'] = df_pool_snaps.snap_vol_usd / df_pool_snaps.snap_tvl_usd
    df_pool_snaps.loc[df_pool_snaps.snap_tvl_usd == 0, 'snap_liq_util'] = 0
    df_pool_snaps.snap_liq_util = df_pool_snaps.snap_liq_util.replace({np.inf: 0}) # TODO: Is this necessary? 
    assert not any(df_pool_snaps.snap_liq_util.isna())
    
    # Same as df_pool_snaps but filtered to only include metapools, then augmented with metapool specific metrics
    df_mpool_snaps = compute_metapool_snaps(df_pools, df_pool_snaps, df_reserves)

    # Cointains global tvl of assets paired against crvFRAX in metapools - primary key (date, pool_coin_address) 
    df_mpool_paired_tokens = (
        df_pool_coin
        .loc[df_pool_coin.pool_coin_address != addresses.token.crvfrax]
        [['pool_coin_name', 'pool_coin_address']]
    )
    token_addr_map = {name: addr for name, addr in df_mpool_paired_tokens.itertuples(index=False)}
    df_mpool_paired_asset_vol = query_metapool_paired_asset_global_volume(cg, token_addr_map)
    df_mpool_paired_asset_vol['pool_coin_address'] = df_mpool_paired_asset_vol.pool_coin_name.apply(lambda name: token_addr_map[name])
    
    df_mpool_snaps = (
        df_mpool_snaps
        # Join the address of the coin that is not crvFRAX onto each mpool snapshot 
        .merge(
            df_coins.loc[df_coins.pool_coin_address != addresses.token.crvfrax]
                [['pool_address', 'pool_coin_address']]
                .rename(columns={'pool_coin_address': 'metapool_asset_address'}), 
            how='left', on=['pool_address']
        ) 
        # For each metapool snapshot, we join in the paired metapool asset and it's global tvl 
        .merge(
            df_mpool_paired_asset_vol
                .rename(columns={'pool_coin_address': 'metapool_asset_address'})
                [['mpool_paired_asset_vol_usd', 'date', 'metapool_asset_address']], 
            how='left', on=['date', 'metapool_asset_address'], 
        )
    )
    df_mpool_snaps.mpool_paired_asset_vol_usd = df_mpool_snaps.mpool_paired_asset_vol_usd.fillna(0)

    # Validation 
    num_metapools = len(df_mpool_snaps.pool_address.unique())
    num_metapools_gauge = len(df_pools.loc[~df_pools.pool_gauge.isna() & (df_pools.pool_fraxbp_metapool == True)])
    print(f"Discovered {num_metapools} metapools.")
    print(f"Number of pools with gauges: {num_metapools_gauge}")    
        
    for table_name, table_df in [
        ('pools', df_pools), 
        ('coins', df_coins), 
        ('pool_coin', df_pool_coin), 
        ('pool_snaps', df_pool_snaps),  
        ('mpool_snaps', df_mpool_snaps), 
        ('reserves', df_reserves), 
    ]:
        df_to_sql.submit(engine, table_df, table_name)
        
    return df_pools, df_coins, df_pool_coin, df_pool_snaps, df_mpool_snaps, df_reserves

In [6]:
df_pools, df_coins, df_pool_coin, df_pool_snaps, df_mpool_snaps, df_reserves = flow_fraxbp_metapool_data()

12:31:09.750 | INFO    | prefect.engine - Created flow run 'thoughtful-wombat' for flow 'flow-fraxbp-metapool-data'

12:31:09.817 | INFO    | Flow run 'thoughtful-wombat' - Created task run 'query_curve_mpools_with_gauge-5c0b2dff-0' for task 'query_curve_mpools_with_gauge'

12:31:09.818 | INFO    | Flow run 'thoughtful-wombat' - Submitted task run 'query_curve_mpools_with_gauge-5c0b2dff-0' for execution.

12:31:09.825 | INFO    | Flow run 'thoughtful-wombat' - Created task run 'query_curve_pool_vol_snapshots-76169dd1-0' for task 'query_curve_pool_vol_snapshots'

12:31:09.826 | INFO    | Flow run 'thoughtful-wombat' - Submitted task run 'query_curve_pool_vol_snapshots-76169dd1-0' for execution.

...

12:31:10.474 | INFO    | Task run 'df_to_sql-2e8b9530-3' - Finished in state Completed()

12:31:10.510 | INFO    | Task run 'df_to_sql-2e8b9530-5' - Finished in state Completed()

12:31:10.517 | INFO    | Task run 'df_to_sql-2e8b9530-2' - Finished in state Completed()

12:31:10.540 | INFO    | Flow run 'thoughtful-wombat' - Finished in state Completed()

sys:1: ResourceWarning: Unclosed socket <zmq.Socket(zmq.PUSH) at 0x29e70bca0>
sys:1: ResourceWarning: Unclosed socket <zmq.Socket(zmq.PUSH) at 0x29f71f640>
sys:1: ResourceWarning: Unclosed socket <zmq.Socket(zmq.PUSH) at 0x177f21780>


In [7]:
# TODO: Show top 19 and aggregate others into single "Other" category.
d_mpool_share = (
    df_mpool_snaps[[
        'date', 'pool_address', 'crvfrax_in_mpool', 'crvfrax_in_all_mpools', 'crvfrax_share_mpools', 'crvfrax_share_fraxbp'
    ]]
    .merge(df_pools[['pool_address', 'pool_symbol']], how='left', on='pool_address')
)
d_mpool_share_last = d_mpool_share.loc[d_mpool_share.date == d_mpool_share.date.max()]

### (Chart) Metapool TVL Share 

- Segmented by pool name 

In [21]:
def chart_mpool_tvl_share(): 
    x = alt.X('date:T', title="date")
    color = alt.Color("pool_symbol:N", scale=alt.Scale(range=colors_28))

    chart_share_of_fraxbp = (
        alt.Chart(d_mpool_share)
        .mark_area()
        .encode(
            x=x, 
            y=alt.Y('crvfrax_share_fraxbp:Q', axis=alt.Axis(format=",%", title="% FraxBP")), 
            color=color, 
            tooltip=["pool_symbol:N", alt.Tooltip('crvfrax_share_fraxbp:Q', format=".1%", title='% FraxBP')]
        )
        .properties(title="Historical Metapool % FraxBP")
    ) 
    chart_share_of_fraxbp_current = (
        alt.Chart(d_mpool_share_last)
        .mark_arc()
        .encode(
            theta='crvfrax_share_fraxbp:Q', 
            color=color, 
            tooltip=["pool_symbol:N", alt.Tooltip('crvfrax_share_fraxbp:Q', format=".1%", title='% FraxBP')]
        )
        .properties(title="Current Metapool % FraxBP")
    )

    chart_metapool_share = (
        alt.Chart(d_mpool_share)
        .mark_area()
        .encode(
            x=x, 
            y=alt.Y('crvfrax_share_mpools:Q', axis=alt.Axis(format=",%", title="% Across Metapools"), scale=alt.Scale(domain=[0,1])), 
            color=color, 
            tooltip=["pool_symbol:N", alt.Tooltip('crvfrax_share_mpools:Q', format=".1%", title='% Across Metapools')]
        )
        .properties(title="Historial Metapool Share Across All Metapools")
    )

    return (chart_share_of_fraxbp | chart_share_of_fraxbp_current | chart_metapool_share)

chart_mpool_tvl_share()

alt.HConcatChart(...)

In [9]:
mpool_addrs = df_pools.loc[df_pools.pool_fraxbp_metapool == True].pool_address.unique()
df_tvl = (
    # Get share of non crvFRAX in each of the metapools 
    df_reserves.loc[
        df_reserves.pool_address.isin(mpool_addrs) & (df_reserves.pool_coin_address != addresses.token.crvfrax)
    ]
    .merge(df_pools[['pool_address', 'pool_type', 'pool_symbol']], how='left', on='pool_address')
)

x = alt.X("date:T", axis=alt.Axis(title="Timestamp"))
color = alt.Color("pool_symbol:N", scale=alt.Scale(range=colors_28))
facet = alt.Facet('pool_type:N', columns=1, header=alt.Header(title=None, labels=False))

# Charts 
chart_tvl_type_breakdown = (
    alt.Chart(df_tvl)
    .transform_aggregate(groupby=['date', 'pool_type'], tvl_pool_type="sum(reserves_usd)")
    .transform_joinaggregate(groupby=['date'], tvl_total="sum(tvl_pool_type)")
    .encode(
        x=x, 
        tooltip=[
            "date:T", 
            "pool_type:N",
            alt.Tooltip("tvl_pool_type:Q", format="$,d"), 
            alt.Tooltip("tvl_total:Q", format="$,d")
        ]
    )
)
chart_tvl_type_breakdown_area = (
    chart_tvl_type_breakdown
    .mark_area()
    .encode(
        y=alt.Y("tvl_pool_type:Q", axis=alt.Axis(title="TVL ($)")), 
        color="pool_type:N",
    )
)
chart_tvl_type_breakdown_line = (
    chart_tvl_type_breakdown
    .mark_line()
    .encode(y="tvl_total:Q")
)

alt.vconcat(
    alt.hconcat(
        (
            alt.Chart(df_tvl)
            .mark_area()
            .encode(
                x=x,
                y=alt.Y("reserves_usd:Q", axis=alt.Axis(title="TVL ($)")), 
                facet=facet, 
                color=color, 
                tooltip=[
                    "date:T", 
                    "pool_symbol:N", 
                    alt.Tooltip("reserves_usd:Q", format="$,d")
                ]
            )
            .resolve_scale(y="independent").resolve_axis("independent")
            .properties(title="Historical Metapool TVL Breakdown")
        ), 
        (
            alt.Chart(
                df_tvl.loc[df_tvl.date == df_tvl.date.max()]
            )
            .mark_arc()
            .encode(
                theta="reserves_usd:Q", 
                color=color, 
                facet=facet, 
                tooltip=[
                    "pool_symbol:N", 
                    alt.Tooltip("reserves_usd:Q", format="$,d", title="TVL"),
                ] 
            )
            .resolve_scale(theta="independent")
            .properties(title="Current Metapool TVL Breakdown")
        )
    ),
    alt.layer(chart_tvl_type_breakdown_area, chart_tvl_type_breakdown_line), 
    center=True
).resolve_legend(color="independent").resolve_scale(color="independent")

/opt/miniconda3/envs/flywheel/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.VConcatChart(...)

### Snapshot Proposals 

We retrieve all snapshot proposals for convex gauge weight snapshots. 

Since votium bribes are intended to get vlCVX holders to vote for particular choices in this snapshot, this data is necessary. 

In [13]:
%load_ext autoreload
%autoreload 2

from flywheel_util.votium_bribes_tasks import (
    query_snapshot_proposals, 
    blocking_query_snapshot_votes_for_proposal, 
    process_snapshot_votes, 
    query_gauge_info, 
    query_votium_epoches, 
    query_votium_bribes, 
    query_bribe_asset_prices, 
    query_votium_claims, 
    process_events_claimed, 
    validate_proposals_vs_epoches, 
    process_df_epoches, 
    label_bribes, 
    join_bribes_choices_epoches_prices, 
    standardize_choices, 
    proposals_to_choices, 
)

/Users/brycemorrow/Documents/code/frax-bribes/flywheel_util/src/flywheel_util/votium_bribes_tasks.py:419: DeprecationWarning: invalid escape sequence '\)'
  if choice in canonical_choices:


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


/opt/miniconda3/envs/flywheel/lib/python3.10/site-packages/prefect/tasks.py:206: UserWarning: A task named 'query_snapshot_proposals' and defined at '/Users/brycemorrow/Documents/code/frax-bribes/flywheel_util/src/flywheel_util/votium_bribes_tasks.py:44' conflicts with another task. Consider specifying a unique `name` parameter in the task definition:

 `@task(name='my_unique_name', ...)`
  warnings.warn(
/opt/miniconda3/envs/flywheel/lib/python3.10/site-packages/prefect/tasks.py:206: UserWarning: A task named 'blocking_query_snapshot_votes_for_proposal' and defined at '/Users/brycemorrow/Documents/code/frax-bribes/flywheel_util/src/flywheel_util/votium_bribes_tasks.py:107' conflicts with another task. Consider specifying a unique `name` parameter in the task definition:

 `@task(name='my_unique_name', ...)`
  warnings.warn(
/opt/miniconda3/envs/flywheel/lib/python3.10/site-packages/prefect/tasks.py:206: UserWarning: A task named 'process_snapshot_votes' and defined at '/Users/brycemor

In [14]:
from prefect.client import get_client

async with get_client() as client:
    # set a concurrency limit of 10 on the 'small_instance' tag
    limit_id = await client.create_concurrency_limit(tag="network_request", concurrency_limit=2)

@flow(cache_result_in_memory=False)
async def flow_votium_votes(): 
    # COINGECKO DATA 
    # ----------------------------------------------------------------
    df_prices = query_bribe_asset_prices.submit()

    # CURVE DATA 
    # ----------------------------------------------------------------
    df_gauge_info = query_gauge_info.submit()
    
    # SNAPSHOT DATA 
    # ----------------------------------------------------------------
    df_proposals = await query_snapshot_proposals()
    df_choices = proposals_to_choices(df_proposals)
    print(f"Number of votium snapshot proposals: {len(df_proposals)}")
    proposal_ids = df_proposals.proposal_id.unique().tolist()
    # Query for data for each proposal independently. The concurrency here is limited 
    # due to constraints of the snapshot api 
    results = [blocking_query_snapshot_votes_for_proposal(pid) for pid in proposal_ids]
    results = await asyncio.gather(*results)
    # Map the proposal id to the count of votes in that proposal 
    for i in range(len(results)): 
        pid = proposal_ids[i]
        # pending votes should not count yet 
        results[i] = [r for r in results[i] if r['vp_state'] == 'final']
        computed_vote_count = len(results[i])
        actual_vote_count = df_proposals.loc[df_proposals.proposal_id == pid].vote_count.values[0]
        assert actual_vote_count == computed_vote_count, "Actual and computed vote counts did not match" 
    print("Here is the count of unique votes per each convex gauge weight snapshot proposal") 
    ddf(df_proposals[['proposal_round', 'vote_count', 'proposal_id']].sort_values('proposal_round').reset_index(drop=True))

    # 
    votes = list(chain(*results)) 
    df_votes = await process_snapshot_votes(votes) # convex gauge votes 
    
    # Join votes with the choice metadata from the snapshot proposal 
    df_votes = df_votes.merge(df_choices, how='left', on=['proposal_id', 'choice_index'], validate="m:1")
    assert not df_votes.proposal_title.isna().any() # ensures each vote was matched with a proposal 
    
    # VOTIUM DATA 
    # ----------------------------------------------------------------
    df_epoches = query_votium_epoches() 
    df_epoches = validate_proposals_vs_epoches(df_proposals, df_epoches)
    df_epoches = process_df_epoches(df_epoches) # must happen after validation to remove erroneous proposal 
    epoch_ids = df_epoches.epoch_id.unique().tolist()
    df_bribes = query_votium_bribes(epoch_ids)
    df_bribes = label_bribes(df_bribes)
    
    events_claimed = query_votium_claims()
    df_claims = process_events_claimed(events_claimed) 

    # Data Joins / Processing 
    # ----------------------------------------------------------------
    # Takes each bribe in fxs or frax and joins the name of the choice voted for, voting round, and prices for reward tokens 
    df_votium_frax = join_bribes_choices_epoches_prices(df_bribes, df_choices, df_epoches, df_prices)
    # Ensures that historical choices map to choices in most recent proposal 
    df_votium_frax = standardize_choices(df_votium_frax, df_gauge_info) 
    
    return df_proposals, df_bribes, df_choices, df_votes, df_epoches, df_prices.result(), df_votium_frax, df_gauge_info.result(), df_claims


/opt/miniconda3/envs/flywheel/lib/python3.10/site-packages/prefect/flows.py:205: UserWarning: A flow named 'flow-votium-votes' and defined at '/var/folders/5c/hf9_blgj3jbbxxvkw_s9snsw0000gn/T/ipykernel_25966/1591415633.py:7' conflicts with another flow. Consider specifying a unique `name` parameter in the flow definition:

 `@flow(name='my_unique_name', ...)`
  warnings.warn(


In [15]:
df_proposals, df_bribes, df_choices, df_votes, df_epoches, df_prices, df_votium_frax, df_gauge_info, df_claims = await flow_votium_votes()

12:38:35.644 | INFO    | prefect.engine - Created flow run 'outstanding-kakapo' for flow 'flow-votium-votes'

12:38:35.697 | INFO    | Flow run 'outstanding-kakapo' - Created task run 'query_bribe_asset_prices-b16c2b4c-0' for task 'query_bribe_asset_prices'

12:38:35.698 | INFO    | Flow run 'outstanding-kakapo' - Submitted task run 'query_bribe_asset_prices-b16c2b4c-0' for execution.

12:38:35.706 | INFO    | Flow run 'outstanding-kakapo' - Created task run 'query_gauge_info-0177b2dd-0' for task 'query_gauge_info'

12:38:35.707 | INFO    | Flow run 'outstanding-kakapo' - Submitted task run 'query_gauge_info-0177b2dd-0' for execution.

...

12:38:45.188 | INFO    | Flow run 'outstanding-kakapo' - Executing 'standardize_choices-57bb53f6-0' immediately...

/Users/brycemorrow/Documents/code/frax-bribes/flywheel_util/src/flywheel_util/votium_bribes_tasks.py:426: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_votium_frax.bribe_choice = df_votium_frax.bribe_choice.apply(preprocess_choice)


12:38:45.228 | INFO    | Task run 'standardize_choices-57bb53f6-0' - Finished in state Completed()

/opt/miniconda3/envs/flywheel/lib/python3.10/site-packages/prefect/utilities/asyncutils.py:233: UserWarning: `sync` called from an asynchronous context; you should `await` the async function directly instead.
  warnings.warn(
sys:1: ResourceWarning: Unclosed socket <zmq.Socket(zmq.PUSH) at 0x29b6544c0>
sys:1: ResourceWarning: Unclosed socket <zmq.Socket(zmq.PUSH) at 0x2ac68a7a0>


12:38:45.353 | INFO    | Flow run 'outstanding-kakapo' - Finished in state Completed()

In [16]:
(
    alt.Chart((
        df_votes[['proposal_round', 'choice', 'choice_vp']]
        .groupby(['proposal_round', 'choice']).sum()
        .reset_index() 
    ))
    .mark_bar()
    .encode(
        x="proposal_round:O", 
        y="choice_vp:Q", 
        color="choice:N", 
        tooltip=["choice:N", "choice_vp:Q"]
    )
    .properties(title="Convex Gauge Weight Vote", width=500) 
)

/opt/miniconda3/envs/flywheel/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.Chart(...)

In [17]:
color = alt.Color('gauge_short_name:N', scale=alt.Scale(range=colors_28))


def chart_bribes_historical(df): 
    return (
        alt.Chart(df)
        .transform_joinaggregate(groupby=['proposal_round'], bribe_amount_total_usd="sum(bribe_amount_usd)")
        .mark_bar()
        .encode(
            x="proposal_round:O", 
            y="bribe_amount_usd:Q", 
            color=color, 
            tooltip=[
                alt.Tooltip('epoch_end_date:T'), 
                alt.Tooltip('gauge_short_name:N'), 
                alt.Tooltip('bribe_token_name:N'),
                alt.Tooltip('bribe_amount:Q', format=",d"),
                alt.Tooltip('bribe_amount_usd:Q', format="$,d"),
                alt.Tooltip('bribe_amount_total_usd:Q', format="$,d"), 
            ]
        )
    )
    
    
def chart_bribes_last_round(df): 
    return (
        alt.Chart(df)
        .mark_arc()
        .encode(
            theta="bribe_amount_usd:Q", 
            color=color, 
            tooltip=['gauge_short_name:N', alt.Tooltip('bribe_amount_usd:Q', format="$,d")]
        )
    )


data = df_votium_frax.copy()
metapool_gauge_addrs = df_pools.loc[df_pools.pool_fraxbp_metapool == True].dropna(subset='pool_gauge').pool_gauge.unique()
data['is_metapool'] = data.gauge_address.apply(lambda addr: addr in metapool_gauge_addrs)

last_round = data.proposal_round.max()
data_last = data.loc[data.proposal_round == last_round]
data_mp = data.loc[data.is_metapool == True] 
data_mp_last = data_mp.loc[data.proposal_round == last_round]

dfp = df_proposals.copy()
dfp.proposal_end = pd.to_datetime(dfp.proposal_end)

# TODO: Bribe for FraxBP in round 26 was using cvxCRV, why is this? 
(
    (chart_bribes_historical(data) | chart_bribes_last_round(data_last)) & 
    (chart_bribes_historical(data_mp) | chart_bribes_last_round(data_mp_last)).resolve_scale(theta='independent', color="shared")
)

/opt/miniconda3/envs/flywheel/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.VConcatChart(...)

In [18]:
first_row(df_pool_snaps)
first_row(df_votium_frax)

In [19]:
# data.head()

In [20]:
# Charts here validated by going to https://curve.fi/#/ethereum/pools
# entering "fraxbp" into the search bar and comparing the tvl of all pools in the UI 
# to the tvl in the charts seen here. 
data = (
    df_mpool_snaps
    .merge(df_pools, how='left', on='pool_address')
    .merge(df_reserves, how='left', on=['pool_address', 'date'])
    .merge(df_coins, how='left', on=['pool_address', 'pool_coin_address'])
)
ncols = 1 
rows = []
row = []
pool_names = data.pool_name.unique().tolist()

# Amount of usd bribes per gauge and round (identified by timestamp) 
df_bribe_gauge_round = df_votium_frax.groupby(['gauge_address', 'epoch_start_date', 'epoch_end_date'])['bribe_amount_usd'].sum().reset_index()

groups = list(data.groupby("pool_name"))
def group_sort_key(g): 
    # Sort by tvl at last time point 
    gdf = g[1]
    return -1 * gdf.loc[gdf.date == gdf.date.max(), 'reserves_usd'].sum()
groups.sort(key=group_sort_key)

for pool_name, sdf in groups: 
    sdf = sdf[[
        'pool_name', 'pool_gauge', 'date', 'reserves_usd', 'snap_tvl_usd', 
        'pool_coin_name', 'snap_vol_usd', 'snap_liq_util', 'mpool_paired_asset_vol_usd', 
    ]]
    sdf = sdf.merge(
        df_bribe_gauge_round, 
        how='left', 
        left_on=['pool_gauge', 'date'], 
        right_on=['gauge_address', 'epoch_end_date'], 
    )
    paired_asset = [e for e in sdf.pool_coin_name.unique() if e != 'crvFRAX'][0]
    
    # For each bribe on the current pool, what is the ratio of bribe / avg_tvl_next_two_weeks mea
    dfb = sdf.loc[sdf.pool_coin_name == 'crvFRAX']
    df_ranges = (
        df_bribe_gauge_round[['epoch_start_date', 'epoch_end_date']]
        .drop_duplicates()
        .sort_values('epoch_start_date').reset_index(drop=True)
    )
    df_ranges['next_epoch_tvl'] = 0
    # map each epoch start to tvl over course of next two weeks 
    epoch_start_to_epoch_tvl = {}
    epoch_end_to_next_epoch_start = {}
    for r in df_ranges.to_dict(orient="records"): 
        s = r['epoch_start_date']
        e = r['epoch_end_date'] 
        df_ranges.loc[df_ranges.epoch_start_date == s, 'next_epoch_tvl'] = (
            dfb.loc[(dfb.date >= s) & (dfb.date < e)].snap_tvl_usd.mean()
        )
    df_ranges = df_ranges.dropna()
    
    # Match each bribe with the tvl of the pool over the next epoch 
    dfb = dfb.merge(df_ranges[['epoch_start_date', 'next_epoch_tvl']], how='left', on='epoch_start_date')
    # Compute ratio of average tvl of pool over next epoch to the bribe 
    dfb['tvl_to_bribe_ratio'] = dfb.next_epoch_tvl / dfb.bribe_amount_usd
    
    # Chart showing TVL in the pool 
    tvl_base = (
        alt.Chart(sdf)
        .transform_calculate(stack_order="datum.pool_coin_name === 'crvFRAX' ? 0 : 1")
        .transform_joinaggregate(groupby=['pool_name', 'date'], tvl_total="sum(reserves_usd)")
        .encode(x="date:T", order="stack_order:O", )
    )
    chart_tvl_area = (
        tvl_base
        .mark_area()
        .encode(
            y=alt.Y("reserves_usd:Q", axis=alt.Axis(title="TVL ($)")), 
            color=alt.Color("pool_coin_name:N", scale=alt.Scale(range=colors_28)), 
            tooltip=[
                alt.Tooltip("pool_coin_name:N"), 
                alt.Tooltip("date:Q", format='$,d'), 
                alt.Tooltip("tvl_total:Q", format='$,d'), 
            ]
        )
    )
    chart_tvl_line = (
        tvl_base
        .transform_filter("datum.pool_coin_name == 'crvFRAX'")
        .mark_line()
        .encode(y="tvl_total:Q")
    )
    chart_pool_liquidity = alt.layer(chart_tvl_area, chart_tvl_line)
    # Chart showing volume in the pool 
    vol_base = (
        alt.Chart(sdf)
        .transform_filter("datum.pool_coin_name !== 'crvFRAX'")
        .encode(x="date:T", order="stack_order:O")
    )
    chart_vol_bar = (
        vol_base
        .mark_bar()
        .encode(
            y="snap_vol_usd:Q", 
            tooltip=[
                alt.Tooltip("snap_vol_usd:Q", format='$,d'), 
            ]
        )
    )
    # Chart showing liquidity utilization in the pool 
    chart_liq_util = (
        vol_base
        .mark_line()
        .encode(
            y=alt.Y("snap_liq_util:Q", scale=alt.Scale(domain=[0,1.0], clamp=True)), 
            tooltip=[
                alt.Tooltip("snap_liq_util:Q", format='$,d'), 
            ]
        )
    )
    # Chart showing ecosystem wide tvl for non crvFRAX assets 
    chart_vol_total = (
        vol_base
        .mark_bar()
        .encode(
            y="mpool_paired_asset_vol_usd:Q", 
            tooltip=[
                alt.Tooltip("mpool_paired_asset_vol_usd:Q", format='$,d'), 
            ]
        )
    )
    # Chart showing ecosystem wide tvl for non crvFRAX assets 
    chart_bribes = (
        vol_base
        .mark_point()
        .encode(
            y="bribe_amount_usd:Q", 
            tooltip=[
                alt.Tooltip("bribe_amount_usd:Q", format='$,d'), 
            ]
        )
    )
    chart_bribe_ratio = (
        alt.Chart(dfb.loc[~dfb.tvl_to_bribe_ratio.isna()])
        .mark_line()
        .encode(
            x="date:T",
            y="tvl_to_bribe_ratio:Q", 
            tooltip=[
                alt.Tooltip("tvl_to_bribe_ratio:Q", format='.2f'), 
            ]
        )
    )

    pool_symbol = pool_name.split(':')[-1].strip()
    w = 250
    h = 150
    
    row.append(
        alt.hconcat(
            chart_pool_liquidity.properties(title=f"TVL: {pool_symbol}", width=w, height=h), 
            chart_liq_util.properties(title=f"Liquidity Utilization (Curve): {pool_symbol}", width=w, height=h), 
            chart_vol_bar.properties(title=f"Volume (Curve): {pool_symbol}", width=w, height=h), 
            chart_vol_total.properties(title=f"Total Volume (Ecosystem): {paired_asset}", width=w, height=h), 
            chart_bribes.properties(title=f"Votium Bribes: {pool_symbol}", width=w, height=h), 
            chart_bribe_ratio.properties(title=f"Votium Bribes Ratio: {pool_symbol}", width=w, height=h), 
            bounds='flush', 
            spacing=75
        )
        .resolve_scale(x="shared")
    )
    if len(row) == ncols: 
        rows.append(row) 
        row = []
    
rows = [
    alt.hconcat(*row) 
    .resolve_scale(x="shared")
    for row in rows
]
chart = (
    alt.vconcat(*rows)
    .resolve_scale(x="shared")
)
chart

/opt/miniconda3/envs/flywheel/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.VConcatChart(...)